# Testes de treinamento incremental

## Abordagem antiga

Nos experimentos anteriores, foi testado diferentes train/test splits e como isso influencia no aprendizado dos modelos. Neles, os algoritmos de MAB iam aprendendo incrementalmente na partição de teste. Porém, nesses experimentos, a partição de teste é sempre modificada ao se mudar o train/test split, gerando problemas para analisar os resultados de diferentes splits.

## Abordagem nova

Abordando o problema de uma forma diferente, agora vamos fazer um train/test split inicial. Depois desse split inicial, parte da partição de treino será selecionado para filtrar a partição de teste (removendo cold-start). Por exemplo, podemos escolher começar apenas com 50% da base de treino, então, será considerado apenas as 50% primeiras interações de treino para fazer a filtragem da partição de teste (removendo os usuários e itens que nunca foram vistos nesses 50% da partição de teste).

Agora, com uma base de teste fixa, vamos treinando os modelos usando diferentes tamanhos da base de treino,. Primeiro, é usado o tamanho que foi utilizado para fazer a filtragem do teste (no exemplo foi 50%), e depois, vamos incrementando esse tamanho de pouco em pouco (por exemplo, podemos incrementar de 5 em 5%, ficando 55%, depois 60%, … e assim por diante, até chegar em 100%).

In [1]:
import pandas as pd
from mab2rec import BanditRecommender, LearningPolicy
from mab2rec.pipeline import train
from sklearn.preprocessing import LabelEncoder
import implicit
from scipy.sparse import csr_matrix
from implicit.nearest_neighbours import bm25_weight
import plotly.express as px
import time
import os

train_data = "../data/ml100k/data_train.csv"
test_data = "../data/ml100k/data_test.csv"

In [2]:
FACTORS = 10
K1 = 100
B = 0.8

In [3]:

def train_embeddings_model(Model, df, num_users, num_items, generate_embeddings=False):
    sparse_matrix = csr_matrix((df['response'], (df['user_id'], df['item_id'])), shape=(num_users, num_items))

    model = Model(factors=FACTORS, random_state=1)
    updated_sparse_matrix = bm25_weight(sparse_matrix, K1=K1, B=B)
    model.fit(updated_sparse_matrix)

    if not generate_embeddings:
        return model, sparse_matrix
    
    user_features_list = []

    for user_id in df['user_id'].unique():
        user_factors = model.user_factors[user_id][:FACTORS]  # O BPR coloca 1 no final dos vetores latentes ?
        user_features_list.append([user_id] + list(user_factors))

    
    df_user_features = pd.DataFrame(user_features_list, columns=['user_id'] + [f'u{i}' for i in range(FACTORS)])

    return model, sparse_matrix, df_user_features

In [6]:

def test_embeddings_model(model, sparse_matrix, df_test):
    all_recs = []

    start_time = time.time()
    hits = 0
    for i, interaction in df_test.iterrows():
        ids_recs, _ = model.recommend(userid=interaction['user_id'], user_items=sparse_matrix[interaction['user_id']], N=10)
        if interaction['item_id'] in ids_recs:
            hits += 1
        all_recs.append(ids_recs.tolist())
    
    recs_df = pd.DataFrame({
        'interaction_number': [i for i in range(len(df_test))],
        'user_id': df_test['user_id'],
        'item_id': df_test['item_id'],
        'recommendations': all_recs
    })
    

    return hits, hits/len(df_test), time.time() - start_time, recs_df

In [5]:

def test_non_incremental(mab_algo, user_features, df_test):
    start_time = time.time()
    hits = 0

    contexts = df_test.merge(user_features, how='left', on='user_id').drop(columns=['user_id', 'item_id', 'response']).values

    print('aaaaaaaaaaaaaaa\n')
    print(contexts)
    recomendations = mab_algo.recommend(contexts)
    print('bbbbbbbbbbbbbb\n')
    print(recomendations)

    df_test = df_test.reset_index(drop=True)

    hits = 0
    for i, interaction in df_test.iterrows():
        if interaction['item_id'] in recomendations[i]:
            hits += 1
    
    recs_df = pd.DataFrame({
        'interaction_number': [i for i in range(len(df_test))],
        'user_id': df_test['user_id'],
        'item_id': df_test['item_id'],
        'recommendations': recomendations
    })

    return hits, hits/len(df_test), time.time() - start_time, recs_df

In [6]:

def test_incremental(mab_algo, user_features, df_test, df_test_for_evaluation, batch_size):
    recs = []

    start_time = time.time()
    hits = 0

    for i in range(0, len(df_test), batch_size):
        # Fazendo recomendações para teste
        df_batch_test = df_test_for_evaluation.loc[i:i+batch_size-1]
        contexts = df_batch_test.merge(user_features, how='left', on='user_id').drop(columns=['user_id', 'item_id', 'response']).values

        if len(contexts) > 0: # Se não tiver nenhuma interação positiva, não faz sentido fazer recomendações
            recomendations = mab_algo.recommend(contexts)
            if isinstance(recomendations, list) and isinstance(recomendations[0], int):
                # Quando o contexto tem tamanho 1, a recomendação é uma lista, e não uma lista de listas
                recomendations = [recomendations]

            df_batch_test = df_batch_test.reset_index(drop=True)

            for j, interaction in df_batch_test.iterrows():
                if interaction['item_id'] in recomendations[j]:
                    hits += 1
            
            recs.extend(recomendations)
        
        # Treinando com o batch
        df_batch_train = df_test.loc[i:i+batch_size-1]
        contexts = df_batch_train.merge(user_features, how='left', on='user_id').drop(columns=['user_id', 'item_id', 'response']).values

        mab_algo.partial_fit(df_batch_train['item_id'], df_batch_train['response'], contexts)
    
    recs_df = pd.DataFrame({
        'interaction_number': [i for i in range(len(df_test_for_evaluation))],
        'user_id': df_test_for_evaluation['user_id'],
        'item_id': df_test_for_evaluation['item_id'],
        'recommendations': recs
    })

    return hits, hits/len(df_test_for_evaluation), time.time() - start_time, recs_df

In [14]:

def test(test_size, train_initial_size, train_increment_step_size):
    '''
    - `test_size`: define o tamanho da partição de teste no train/test split inicial. Por exemplo, se for escolhido 0.1 (10%), a partição de teste terá 10% das interações e a partição de treino terá 90% das interações. O tamanho da partição de teste passará ainda por um filtro com o tamanho do treino inicial, definido no próximo parâmetro.
    - `train_initial_size`: define o tamanho inicial que será usado para treino dos modelos. Esse tamanho é uma porcentagem da partição de treino, por exemplo, 0.5 (50%) quer dizer que o treino será feito inicialmente com 50% das interações separadas para treino. Vale ressaltar que essa porcentagem é relacionada apenas à partição de treino, então, se temos uma partição de treino de 0.9 (90%) e o “train_initial_size” é definido como 0.5 (50%), então, teremos 45% (0.9 * 0.5) das interações todas para o treino inicial. Com a base de treino separada com essa porcentagem inicial, a base de teste passara por um filtro, removendo todas as interações com itens ou usuários que nunca foram vistos nesse treino inicial.
    - `train_increment_step_size`: define de quanto em quanto a base de treino irá crescer para o treino dos modelos. Esse incremento será feito sobre o tamanho inicial de treino. Por exemplo, se temos “train_initial_size” como 0.5 (50%), e temos “train_increment_step_size” como 0.05 (5%), então, iremos incrementar para 55%, depois para 60%, … e assim por diante até chegar em 100%.
    '''
    results = []
    df_recs = pd.DataFrame(columns=['algorithm', 'interaction_number', 'user_id', 'item_id', 'recommendations'])
    df_train = pd.read_csv(train_data)
    df_test = pd.read_csv(test_data)

    df_full = pd.concat([df_train, df_test])

    df_full['user_id'] = LabelEncoder().fit_transform(df_full['user_id'])
    df_full['item_id'] = LabelEncoder().fit_transform(df_full['item_id'])

    num_users = df_full['user_id'].nunique()
    num_items = df_full['item_id'].nunique()

    split_index = int(len(df_full) * (1 - test_size))
    df_train_full = df_full[:split_index]
    df_test = df_full[split_index:]

    print('xxxxx')
    print(df_train_full)

    current_df_train = df_train_full[:int(len(df_train_full) * train_initial_size)]

    df_test = df_test[(df_test['user_id'].isin(current_df_train['user_id'])) & (df_test['item_id'].isin(current_df_train['item_id']))]
    df_test = df_test.reset_index(drop=True)
    df_test_for_evaluation = df_test[df_test['response'] == 1]

    print('Generating ALS embeddings')
    ALS_model, _, ALS_user_features = train_embeddings_model(implicit.als.AlternatingLeastSquares, current_df_train, num_users, num_items, generate_embeddings=True)

    print('Generating BPR embeddings')
    BPR_model, _, BPR_user_features = train_embeddings_model(implicit.bpr.BayesianPersonalizedRanking, current_df_train, num_users, num_items, generate_embeddings=True)

    current_train_size = train_initial_size
    while current_train_size <= 1:
        print(f"Current train size: {current_train_size}")

        current_df_train = df_train_full[:int(len(df_train_full) * current_train_size)]

        # -------------- ALS -----------------
        print('Training ALS')
        ALS_model, sparse_matrix = train_embeddings_model(implicit.als.AlternatingLeastSquares, current_df_train, num_users, num_items)

        print('Testing ALS')
        hits, hr, spent_time, df_recs_als = test_embeddings_model(ALS_model, sparse_matrix, df_test_for_evaluation)
        df_recs_als['algorithm'] = 'ALS'
        df_recs_als['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_als])
        results.append({'algorithm': 'ALS', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # -------------- BPR -----------------
        print('Training BPR')
        BPR_model, sparse_matrix = train_embeddings_model(implicit.bpr.BayesianPersonalizedRanking, current_df_train, num_users, num_items)

        print('Testing BPR')
        hits, hr, spent_time, df_recs_bpr = test_embeddings_model(BPR_model, sparse_matrix, df_test_for_evaluation)
        df_recs_bpr['algorithm'] = 'BPR'
        df_recs_bpr['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_bpr])
        results.append({'algorithm': 'BPR', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})

        print('oppaaaaaaaa')
        print(current_df_train)

        # ------ LinUCB - non-incremental - ALS embeddings -------
        print('Training LinUCB - non-incremental - ALS embeddings')
        linUCB_model = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
        train(linUCB_model, data=current_df_train, user_features=ALS_user_features)

        print('Testing LinUCB - non-incremental - ALS embeddings')
        hits, hr, spent_time, df_recs_linUCB = test_non_incremental(linUCB_model, ALS_user_features, df_test_for_evaluation)
        df_recs_linUCB['algorithm'] = 'LinUCB - non-incremental - ALS embeddings'
        df_recs_linUCB['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linUCB])
        results.append({'algorithm': 'LinUCB - non-incremental - ALS embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinUCB - non-incremental - BPR embeddings -------
        print('Training LinUCB - non-incremental - BPR embeddings')
        linUCB_model = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
        train(linUCB_model, data=current_df_train, user_features=BPR_user_features)

        print('Testing LinUCB - non-incremental - BPR embeddings')
        hits, hr, spent_time, df_recs_linUCB = test_non_incremental(linUCB_model, BPR_user_features, df_test_for_evaluation)
        df_recs_linUCB['algorithm'] = 'LinUCB - non-incremental - BPR embeddings'
        df_recs_linUCB['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linUCB])
        results.append({'algorithm': 'LinUCB - non-incremental - BPR embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinUCB - incremental - ALS embeddings -------
        print('Training LinUCB - incremental - ALS embeddings')
        linUCB_model = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
        train(linUCB_model, data=current_df_train, user_features=ALS_user_features)

        print('Testing LinUCB - incremental - ALS embeddings')
        hits, hr, spent_time, df_recs_linUCB = test_incremental(linUCB_model, ALS_user_features, df_test, df_test_for_evaluation, batch_size=10)
        df_recs_linUCB['algorithm'] = 'LinUCB - incremental - ALS embeddings'
        df_recs_linUCB['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linUCB])
        results.append({'algorithm': 'LinUCB - incremental - ALS embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinUCB - incremental - BPR embeddings -------
        print('Training LinUCB - incremental - BPR embeddings')
        linUCB_model = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
        train(linUCB_model, data=current_df_train, user_features=BPR_user_features)

        print('Testing LinUCB - incremental - BPR embeddings')
        hits, hr, spent_time, df_recs_linUCB = test_incremental(linUCB_model, BPR_user_features, df_test, df_test_for_evaluation, batch_size=10)
        df_recs_linUCB['algorithm'] = 'LinUCB - incremental - BPR embeddings'
        df_recs_linUCB['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linUCB])
        results.append({'algorithm': 'LinUCB - incremental - BPR embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinGreedy - non-incremental - ALS embeddings -------
        print('Training LinGreedy - non-incremental - ALS embeddings')
        linGreedy_model = BanditRecommender(learning_policy=LearningPolicy.LinGreedy(epsilon=0.01), top_k=10)
        train(linGreedy_model, data=current_df_train, user_features=ALS_user_features)

        print('Testing LinGreedy - non-incremental - ALS embeddings')
        hits, hr, spent_time, df_recs_linGreedy = test_non_incremental(linGreedy_model, ALS_user_features, df_test_for_evaluation)
        df_recs_linGreedy['algorithm'] = 'LinGreedy - non-incremental - ALS embeddings'
        df_recs_linGreedy['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linGreedy])
        results.append({'algorithm': 'LinGreedy - non-incremental - ALS embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinGreedy - non-incremental - BPR embeddings -------
        print('Training LinGreedy - non-incremental - BPR embeddings')
        linGreedy_model = BanditRecommender(learning_policy=LearningPolicy.LinGreedy(epsilon=0.01), top_k=10)
        train(linGreedy_model, data=current_df_train, user_features=BPR_user_features)

        print('Testing LinGreedy - non-incremental - BPR embeddings')
        hits, hr, spent_time, df_recs_linGreedy = test_non_incremental(linGreedy_model, BPR_user_features, df_test_for_evaluation)
        df_recs_linGreedy['algorithm'] = 'LinGreedy - non-incremental - BPR embeddings'
        df_recs_linGreedy['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linGreedy])
        results.append({'algorithm': 'LinGreedy - non-incremental - BPR embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinGreedy - incremental - ALS embeddings -------
        print('Training LinGreedy - incremental - ALS embeddings')
        linGreedy_model = BanditRecommender(learning_policy=LearningPolicy.LinGreedy(epsilon=0.01), top_k=10)
        train(linGreedy_model, data=current_df_train, user_features=ALS_user_features)

        print('Testing LinGreedy - incremental - ALS embeddings')
        hits, hr, spent_time, df_recs_linGreedy = test_incremental(linGreedy_model, ALS_user_features, df_test, df_test_for_evaluation, batch_size=10)
        df_recs_linGreedy['algorithm'] = 'LinGreedy - incremental - ALS embeddings'
        df_recs_linGreedy['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linGreedy])
        results.append({'algorithm': 'LinGreedy - incremental - ALS embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})


        # ------ LinGreedy - incremental - BPR embeddings -------
        print('Training LinGreedy - incremental - BPR embeddings')
        linGreedy_model = BanditRecommender(learning_policy=LearningPolicy.LinGreedy(epsilon=0.01), top_k=10)
        train(linGreedy_model, data=current_df_train, user_features=BPR_user_features)

        print('Testing LinGreedy - incremental - BPR embeddings')
        hits, hr, spent_time, df_recs_linGreedy = test_incremental(linGreedy_model, BPR_user_features, df_test, df_test_for_evaluation, batch_size=10)
        df_recs_linGreedy['algorithm'] = 'LinGreedy - incremental - BPR embeddings'
        df_recs_linGreedy['train_size'] = current_train_size
        df_recs = pd.concat([df_recs, df_recs_linGreedy])
        results.append({'algorithm': 'LinGreedy - incremental - BPR embeddings', 'hits': hits, 'hr': hr, 'time': spent_time, 'train_size': current_train_size})
        
        # Incrementando o tamanho do treino para próxima iteração
        current_train_size = round(current_train_size + train_increment_step_size, 2)
    
    save_path = f'results-v4/'
    if not os.path.exists(save_path):
        os.makedirs(save_path)

    df_results = pd.DataFrame(results)
    df_results = df_results.astype({'hits': int, 'hr': float, 'time': float})
    df_results['test_size'] = round(test_size, 2)
    df_results['test_interactions'] = len(df_test_for_evaluation)

    df_results.to_csv(f'{save_path}/results2.csv', index=False)
    df_recs.to_csv(f'{save_path}/recs2.csv', index=False)

In [15]:
test(test_size=0.1, train_initial_size=0.5, train_increment_step_size=0.05)

xxxxx
     user_id  item_id  response
0        842      154         0
1        143       59         1
2        600      103         0
3        750      199         0
4        200      116         0
..       ...      ...       ...
858      345      133         1
859      345       81         0
860      345       33         0
861      345        5         0
862      345       19         0

[35406 rows x 3 columns]
Generating ALS embeddings


c:\Users\gregf\anaconda3\envs\RLRS-rllib\lib\site-packages\implicit\utils.py:138: ParameterWarning:

Method expects CSR input, and was passed coo_matrix instead. Converting to CSR took 0.0 seconds



  0%|          | 0/15 [00:00<?, ?it/s]

Generating BPR embeddings


c:\Users\gregf\anaconda3\envs\RLRS-rllib\lib\site-packages\implicit\utils.py:138: ParameterWarning:

Method expects CSR input, and was passed coo_matrix instead. Converting to CSR took 0.0020084381103515625 seconds



...

  0%|          | 0/15 [00:00<?, ?it/s]

Testing ALS
Training BPR


c:\Users\gregf\anaconda3\envs\RLRS-rllib\lib\site-packages\implicit\utils.py:138: ParameterWarning:

Method expects CSR input, and was passed coo_matrix instead. Converting to CSR took 0.0 seconds



  0%|          | 0/100 [00:00<?, ?it/s]

Testing BPR
oppaaaaaaaa
     user_id  item_id  response
0        842      154         0
1        143       59         1
2        600      103         0
3        750      199         0
4        200      116         0
..       ...      ...       ...
858      345      133         1
859      345       81         0
860      345       33         0
861      345        5         0
862      345       19         0

[35406 rows x 3 columns]
Training LinUCB - non-incremental - ALS embeddings
Testing LinUCB - non-incremental - ALS embeddings
aaaaaaaaaaaaaaa

[[ 0.3126468   0.47124487  0.10370017 ... -0.38419256 -0.08413794
   0.20778592]
 [ 0.3126468   0.47124487  0.10370017 ... -0.38419256 -0.08413794
   0.20778592]
 [ 0.3126468   0.47124487  0.10370017 ... -0.38419256 -0.08413794
   0.20778592]
 ...
 [ 1.2880335   0.06063697 -1.2275593  ...  1.2927729   0.17856306
  -0.05261376]
 [ 0.70115834  0.8614948   0.9834923  ...  0.07909627  1.9146004
   0.73441696]
 [ 1.1967105   1.8336424   0.20737484 .

In [24]:
df_results = pd.read_csv('results-v4/results.csv')

In [25]:
fig = px.line(df_results, x="train_size", y="hr", color='algorithm', title='HR x Train size')
fig.show()
fig.write_html('results-v4/hr_x_train_size.html')

In [4]:
testing_df1 = pd.DataFrame(
    {
        'x': [1, 2, 2, 1],
        'y': ['a', 'b', 'c', 'd'],
    }
)

testing_df2 = pd.DataFrame(
    {
        'x': [1, 2],
        'z': ['A', 'B'],
    }
)

print(testing_df1.merge(testing_df2, how='inner', on='x'))

   x  y  z
0  1  a  A
1  1  d  A
2  2  b  B
3  2  c  B


In [5]:
df_recs = pd.DataFrame(columns=['algorithm', 'interaction_number', 'user_id', 'item_id', 'recommendations'])
df_train = pd.read_csv(train_data)
df_test = pd.read_csv(test_data)

df_full = pd.concat([df_train, df_test])

df_full['user_id'] = LabelEncoder().fit_transform(df_full['user_id'])
df_full['item_id'] = LabelEncoder().fit_transform(df_full['item_id'])

num_users = df_full['user_id'].nunique()
num_items = df_full['item_id'].nunique()

split_index = int(len(df_full) * (1 - 0.1))
df_train_full = df_full[:split_index]
df_test = df_full[split_index:]

In [6]:
current_df_train = df_train_full[:int(len(df_train_full) * 0.5)]

df_test = df_test[(df_test['user_id'].isin(current_df_train['user_id'])) & (df_test['item_id'].isin(current_df_train['item_id']))]
df_test = df_test.reset_index(drop=True)
df_test_for_evaluation = df_test[df_test['response'] == 1]

print('Generating ALS embeddings')
ALS_model, _, ALS_user_features = train_embeddings_model(implicit.als.AlternatingLeastSquares, current_df_train, num_users, num_items, generate_embeddings=True)

print('Generating BPR embeddings')
BPR_model, _, BPR_user_features = train_embeddings_model(implicit.bpr.BayesianPersonalizedRanking, current_df_train, num_users, num_items, generate_embeddings=True)

Generating ALS embeddings


c:\Users\gregf\anaconda3\envs\RLRS-rllib\lib\site-packages\implicit\utils.py:138: ParameterWarning: Method expects CSR input, and was passed coo_matrix instead. Converting to CSR took 0.0 seconds
  warnings.warn(


  0%|          | 0/15 [00:00<?, ?it/s]

Generating BPR embeddings


c:\Users\gregf\anaconda3\envs\RLRS-rllib\lib\site-packages\implicit\utils.py:138: ParameterWarning: Method expects CSR input, and was passed coo_matrix instead. Converting to CSR took 0.0 seconds
  warnings.warn(


  0%|          | 0/100 [00:00<?, ?it/s]

In [7]:
linUCB_model_1 = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
train(linUCB_model_1, data=current_df_train, user_features=BPR_user_features)

[[-4.92529988e-01  4.58438307e-01 -1.38673335e-01 -5.64996541e-01
   1.36743829e-01 -4.42527592e-01 -7.61322975e-01 -8.22976530e-01
   4.27425802e-01 -1.25404214e-02]
 [-6.38635993e-01  3.01049054e-01  1.43142566e-01 -1.02665879e-01
  -8.68120715e-02  2.25760221e-01 -3.74518454e-01 -5.47865927e-01
  -4.53930438e-01  5.71733057e-01]
 [-6.24306202e-01 -7.22630844e-02  2.44603217e-01  6.18357658e-02
  -1.45733774e-01  4.48578060e-01 -5.94044864e-01 -8.67122293e-01
   2.71271199e-01 -2.34969303e-01]
 [ 6.90099224e-02 -4.28436190e-01  1.97541714e-01 -2.22963616e-01
  -4.70180184e-01 -6.20561838e-02 -8.79001379e-01 -7.51000345e-02
   7.59351671e-01  8.41519296e-01]
 [ 5.89956880e-01  1.86711876e-03  8.32065418e-02  3.74211609e-01
   4.12182122e-01  6.17266238e-01 -3.60480756e-01 -5.62126994e-01
  -6.76322281e-01 -5.49407005e-01]
 [-1.62385508e-01 -4.54853773e-01  3.86881560e-01  3.02197993e-01
  -5.44975340e-01  8.09846401e-01 -3.09570879e-01 -6.21401489e-01
   2.95860674e-02 -2.22330034e-01

In [8]:
linUCB_model_1.recommend([BPR_user_features.iloc[4, 1:].values], return_scores=True)

([133, 16, 68, 163, 189, 169, 3, 57, 67, 84],
 [0.7001398483447949,
  0.670637784366891,
  0.647737280094413,
  0.6412255246386648,
  0.6374085138484605,
  0.6290378093014241,
  0.6191169877638732,
  0.6164498450280487,
  0.6142457069829889,
  0.6120818227663051])

In [9]:
linUCB_model_2 = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
train(linUCB_model_2, data=df_train_full, user_features=BPR_user_features)

[[-0.49253     0.4584383  -0.13867334 ... -0.8229765   0.4274258
  -0.01254042]
 [-0.638636    0.30104905  0.14314257 ... -0.5478659  -0.45393044
   0.57173306]
 [-0.6243062  -0.07226308  0.24460322 ... -0.8671223   0.2712712
  -0.2349693 ]
 ...
 [-0.1319181   0.18539874  0.02275272 ...  0.18090819  0.05745022
   0.01277399]
 [        nan         nan         nan ...         nan         nan
          nan]
 [        nan         nan         nan ...         nan         nan
          nan]]
[nan nan nan nan nan nan nan nan nan nan]
[[ 8.6830032e-01 -7.6976478e-01  3.2552078e-01 ...  1.3231735e-01
   3.8774878e-01 -4.0728293e-02]
 [ 1.2942114e-02 -1.7986822e-01 -5.2734500e-01 ... -6.2314101e-02
  -2.0680724e-01 -6.2355959e-01]
 [-1.0435171e+00 -8.0889392e-01 -1.9215703e-01 ... -3.8281906e-01
  -2.8199400e-04  3.7844531e-02]
 ...
 [           nan            nan            nan ...            nan
             nan            nan]
 [           nan            nan            nan ...            nan
 

In [10]:
linUCB_model_2.recommend([BPR_user_features.iloc[20, 1:].values], return_scores=True)

([196, 18, 39, 63, 85, 182, 57, 73, 143, 82],
 [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan])

In [31]:
linUCB_model_3 = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
train(linUCB_model_3, data=df_train_full[:int(len(df_train_full) * 0.65)], user_features=BPR_user_features)

[[-0.49253     0.4584383  -0.13867334 ... -0.8229765   0.4274258
  -0.01254042]
 [-0.638636    0.30104905  0.14314257 ... -0.5478659  -0.45393044
   0.57173306]
 [-0.6243062  -0.07226308  0.24460322 ... -0.8671223   0.2712712
  -0.2349693 ]
 ...
 [-0.61443704 -0.18783814  0.02925627 ... -0.5378612  -0.545745
   0.87297845]
 [-0.42827713 -0.37050322  0.2280357  ... -1.0264982   0.26692766
   0.31446645]
 [ 0.43996477  0.30109248 -0.32597074 ...  0.07827755 -0.01406553
  -0.05415572]]
[ 0.04399512  0.05250452  0.27153212  0.01907233  0.2032756   0.25289037
 -0.10333529 -0.40341313 -0.1772434   0.25474946]
[[ 8.6830032e-01 -7.6976478e-01  3.2552078e-01 ...  1.3231735e-01
   3.8774878e-01 -4.0728293e-02]
 [ 1.2942114e-02 -1.7986822e-01 -5.2734500e-01 ... -6.2314101e-02
  -2.0680724e-01 -6.2355959e-01]
 [-1.0435171e+00 -8.0889392e-01 -1.9215703e-01 ... -3.8281906e-01
  -2.8199400e-04  3.7844531e-02]
 ...
 [ 2.9801553e-01  2.6647153e-01 -6.3872361e-01 ... -1.1020653e+00
   3.2662377e-01  5.2

In [32]:
linUCB_model_3.recommend([BPR_user_features.iloc[20, 1:].values], return_scores=True)

([123, 164, 150, 108, 101, 137, 78, 193, 154, 29],
 [nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  0.6986267689739871,
  0.6428197148384522,
  0.6311589074377276,
  0.6165273976335591])

In [33]:
linUCB_model_4 = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
train(linUCB_model_4, data=df_train_full[:int(len(df_train_full) * 0.7)], user_features=BPR_user_features)

[[-0.49253     0.4584383  -0.13867334 ... -0.8229765   0.4274258
  -0.01254042]
 [-0.638636    0.30104905  0.14314257 ... -0.5478659  -0.45393044
   0.57173306]
 [-0.6243062  -0.07226308  0.24460322 ... -0.8671223   0.2712712
  -0.2349693 ]
 ...
 [-0.6382107  -0.5581729  -0.07956798 ... -0.26315984  0.07626376
  -0.44727176]
 [-0.6122685   0.50843537 -0.2171514  ... -0.6085535   0.6032595
   0.09656683]
 [-0.3575107   0.32744595  0.01981828 ... -1.4265531  -0.34982082
  -0.62945914]]
[nan nan nan nan nan nan nan nan nan nan]
[[ 8.6830032e-01 -7.6976478e-01  3.2552078e-01 ...  1.3231735e-01
   3.8774878e-01 -4.0728293e-02]
 [ 1.2942114e-02 -1.7986822e-01 -5.2734500e-01 ... -6.2314101e-02
  -2.0680724e-01 -6.2355959e-01]
 [-1.0435171e+00 -8.0889392e-01 -1.9215703e-01 ... -3.8281906e-01
  -2.8199400e-04  3.7844531e-02]
 ...
 [-4.5670232e-01 -4.3426552e-01  2.7197292e-01 ... -2.7875024e-01
   3.6804682e-01 -5.0968146e-01]
 [ 3.2411146e-01  3.3928114e-01 -3.3403906e-01 ... -7.3724854e-01
  

In [34]:
linUCB_model_4.recommend([BPR_user_features.iloc[20, 1:].values], return_scores=True)

([154, 101, 97, 108, 79, 150, 137, 164, 139, 123],
 [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan])

In [35]:
linUCB_model_5 = BanditRecommender(learning_policy=LearningPolicy.LinUCB(alpha=0.1), top_k=10)
train(linUCB_model_5, data=df_train_full[:int(len(df_train_full) * 0.9)], user_features=BPR_user_features)

[[-0.49253     0.4584383  -0.13867334 ... -0.8229765   0.4274258
  -0.01254042]
 [-0.638636    0.30104905  0.14314257 ... -0.5478659  -0.45393044
   0.57173306]
 [-0.6243062  -0.07226308  0.24460322 ... -0.8671223   0.2712712
  -0.2349693 ]
 ...
 [-0.11965899 -0.27267852 -0.12883615 ... -1.1552849   0.07883607
   0.152012  ]
 [-0.34636223  0.7087003   0.20517598 ... -0.2282073  -0.20244364
   0.1248719 ]
 [ 0.34733114 -0.52453244 -0.7045902  ...  0.3486718   0.3216532
  -0.55478054]]
[nan nan nan nan nan nan nan nan nan nan]
[[ 8.68300319e-01 -7.69764781e-01  3.25520784e-01 ...  1.32317349e-01
   3.87748778e-01 -4.07282934e-02]
 [ 1.29421139e-02 -1.79868221e-01 -5.27345002e-01 ... -6.23141006e-02
  -2.06807241e-01 -6.23559594e-01]
 [-1.04351711e+00 -8.08893919e-01 -1.92157030e-01 ... -3.82819057e-01
  -2.81993998e-04  3.78445312e-02]
 ...
 [-1.78936794e-01  1.23669624e-01 -1.36055380e-01 ... -1.19001977e-01
   2.80569851e-01  8.02776456e-01]
 [-3.21214944e-01 -1.84920341e-01  2.6573354

In [40]:
linUCB_model_5.recommend([BPR_user_features.iloc[0, 1:].values], return_scores=True)

([154, 133, 123, 150, 138, 101, 122, 141, 33, 137],
 [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan])